In [1]:
import numpy as np
from ipywidgets import IntSlider, SelectionSlider, Checkbox, Text, \
    interactive_output, VBox, HBox, HTMLMath, Layout


**Learning goals:**

- Be able to describe the behavior, both short-term and long-term, for any discrete-time linear model whose matrix is ***diagonal***. 
- For such a model, be able to determine which axis the long-term behavior will grow or decay parallel to. 


**Discrete-time linear model, with a diagonal matrix:**

$$ \begin{bmatrix} X_{t+1} \\ Y_{t+1} \end{bmatrix} = \begin{pmatrix} a & 0 \\ 0 & d \end{pmatrix} \begin{bmatrix} X_t \\ Y_t \end{bmatrix} $$

or

$$ \begin{cases}
    X_{t+1} = a X_t \\
    Y_{t+1} = d Y_t
\end{cases} $$


Solution: 

$$X_t = X_0 a^t \qquad \text{and} \qquad Y_t = Y_0 d^t$$


In [2]:
def colorchoice(a):
    return "green" if abs(a) < 1 else "red" if abs(a) > 1 else "purple"


In [3]:
def diagonal_interactive(eigenvalues, initial_state=None):
    axismax = 10
    tmax = 50
    D = diagonal_matrix(RDF, eigenvalues)
    def initchoice(a):
        if abs(a) < 1:
            return round((0.8 + uniform(-0.2, 0.2))*axismax, 1)
        if abs(a) > 1:
            return round((0.2 + uniform(-0.2, 0.2))*axismax, 1)
        return round(uniform(0, axismax), 1)
    if initial_state is None:
        initial_state = vector([initchoice(eigenvalues[0]), initchoice(eigenvalues[1])])
    else:
        initial_state = vector(initial_state)
    solution = np.array([D^t * initial_state for t in range(tmax+1)], dtype=float)

    dont_update = False
    def update(t, xt, yt, showlines, axismax):
        if dont_update:
            return
        p = list_plot(solution[:t+1], size=30, color="black")
        p += list_plot(solution[:t+1], plotjoined=True, color="gray")
        p += list_plot(solution[:xt+1] * (1,0), size=30, color=colorchoice(eigenvalues[0]))
        p += list_plot(solution[:yt+1] * (0,1), size=30, color=colorchoice(eigenvalues[1]))
        if showlines:
            x0, y0 = solution[t]
            p += line(((x0,0), (x0,y0), (0,y0)), color="lightgray")
            p += point((x0,0), size=50, color=colorchoice(eigenvalues[0]))
            p += point((0,y0), size=50, color=colorchoice(eigenvalues[1]))
        p.show(xmin=-axismax, xmax=axismax, ymin=-axismax, ymax=axismax, 
               axes_labels=("$X$", "$Y$"), aspect_ratio=1, figsize=9.5)

    def change_initial_state(change):
        nonlocal dont_update, solution
        initial_state = change["new"].strip("()[]").split(",")
        try:
            initial_state = vector([float(x) for x in initial_state])
            solution = np.array([D^t * initial_state for t in range(tmax+1)], dtype=float)
        except:
            return
        dont_update = True
        t.value = 1
        xt.value = 0
        yt.value = 0
        dont_update = False
        t.value = 0

    layout = Layout(width="250px", margin="15px 0px 15px 0px")
    label = (r"$$\begin{bmatrix} X_{t+1} \\ Y_{t+1} \end{bmatrix} = %s "
             r"\begin{bmatrix} X_t \\ Y_t \end{bmatrix}$$")
    equation = HTMLMath(label % latex(D), layout=layout)
    t  = IntSlider(min=0, max=tmax, layout=layout, description="Sol'n steps:")
    xt = IntSlider(min=0, max=tmax, layout=layout, description="X steps:")
    yt = IntSlider(min=0, max=tmax, layout=layout, description="Y steps:")
    showlines = Checkbox(value=False, layout=layout, description="Show XY lines")
    zoom = SelectionSlider(options=[1, 10, 20, 50, 100, 200, 500, 1000], value=10, 
                           layout=layout, description="Zoom:")
    state = Text(value=str(initial_state), continuous_update=False, 
                 layout=layout, description="Initial state:")
    state.observe(change_initial_state, "value")
    output = interactive_output(update, dict(t=t, xt=xt, yt=yt, showlines=showlines, axismax=zoom))
    controls = VBox((equation, state, t, xt, yt, showlines, zoom))
    display(HBox((controls, output)))


In [4]:
diagonal_interactive((1.08, 0.9))

In [5]:
diagonal_interactive((0.95, 1.2))

<table>
    <tr><th>$X$ rate</th> <th>$Y$ rate</th> <th>Eq. pt. at $(0,0)$</th> <th>Long term behavior</th></tr>
    <tr><td>1.08</td> <td>0.9</td> <td>Saddle point</td> <td>Exp. growth along $X$ axis</td> </tr>
    <tr><td>0.95</td> <td>1.2</td> <td>Saddle point</td> <td>Exp. growth along $Y$ axis</td> </tr>
</table>


In [6]:
diagonal_interactive((0.9, 0.4))

In [7]:
diagonal_interactive((0.85, 0.9))

<table>
    <tr><th>$X$ rate</th> <th>$Y$ rate</th> <th>Eq. pt. at $(0,0)$</th> <th>Long term behavior</th></tr>
    <tr><td>1.08</td> <td>0.9 </td> <td>Saddle point</td> <td>Exp. growth along $X$ axis</td> </tr>
    <tr><td>0.95</td> <td>1.2 </td> <td>Saddle point</td> <td>Exp. growth along $Y$ axis</td> </tr>
    <tr><td>0.9 </td> <td>0.4 </td> <td>Sink        </td> <td>Exp. decay  along $X$ axis</td> </tr>
    <tr><td>0.85</td> <td>0.9 </td> <td>Sink        </td> <td>Exp. decay  along $Y$ axis</td> </tr>
</table>


In [8]:
diagonal_interactive((1.2, 1.1))

<table>
    <tr><th>$X$ rate</th> <th>$Y$ rate</th> <th>Eq. pt. at $(0,0)$</th> <th>Long term behavior</th></tr>
    <tr><td>1.08</td> <td>0.9 </td> <td>Saddle point</td> <td>Exp. growth along $X$ axis</td> </tr>
    <tr><td>0.95</td> <td>1.2 </td> <td>Saddle point</td> <td>Exp. growth along $Y$ axis</td> </tr>
    <tr><td>0.9 </td> <td>0.4 </td> <td>Sink        </td> <td>Exp. decay  along $X$ axis</td> </tr>
    <tr><td>0.85</td> <td>0.9 </td> <td>Sink        </td> <td>Exp. decay  along $Y$ axis</td> </tr>
    <tr><td>1.2 </td> <td>1.1 </td> <td>Source      </td> <td>Exp. growth parallel to $X$ axis</td> </tr>
</table>


In [9]:
diagonal_interactive((1.5, 1.5))

In [10]:
diagonal_interactive((-0.8, 1.1))

In [11]:
diagonal_interactive((-0.8, 0.5))

<table>
    <tr><th>$X$ rate</th> <th>$Y$ rate</th> <th>Eq. pt. at $(0,0)$</th> <th>Long term behavior</th></tr>
    <tr><td> 1.08</td> <td> 0.9 </td> <td>Saddle point</td> <td>Exp. growth along $X$ axis</td> </tr>
    <tr><td> 0.95</td> <td> 1.2 </td> <td>Saddle point</td> <td>Exp. growth along $Y$ axis</td> </tr>
    <tr><td> 0.9 </td> <td> 0.4 </td> <td>Sink        </td> <td>Exp. decay  along $X$ axis</td> </tr>
    <tr><td> 0.85</td> <td> 0.9 </td> <td>Sink        </td> <td>Exp. decay  along $Y$ axis</td> </tr>
    <tr><td> 1.2 </td> <td> 1.1 </td> <td>Source      </td> <td>Exp. growth parallel to $X$ axis</td> </tr>
    <tr><td> 1.5 </td> <td> 1.5 </td> <td>Source      </td> <td>Exp. growth in all directions</td> </tr>
    <tr><td>-0.8 </td> <td> 1.1 </td> <td>Saddle      </td> <td>Exp. growth along $Y$ axis</td> </tr>
    <tr><td>-0.8 </td> <td> 0.5 </td> <td>Sink        </td> <td>Fluctuating exp. decay along $X$ axis!</td> </tr>
</table>


In [12]:
diagonal_interactive((0.95, -1.1))

In [13]:
diagonal_interactive((-0.8, -1.2))

<table>
    <tr><th>$X$ rate</th> <th>$Y$ rate</th> <th>Eq. pt. at $(0,0)$</th> <th>Long term behavior</th></tr>
    <tr><td> 1.08</td> <td> 0.9 </td> <td>Saddle point</td> <td>Exp. growth along $X$ axis</td> </tr>
    <tr><td> 0.95</td> <td> 1.2 </td> <td>Saddle point</td> <td>Exp. growth along $Y$ axis</td> </tr>
    <tr><td> 0.9 </td> <td> 0.4 </td> <td>Sink        </td> <td>Exp. decay  along $X$ axis</td> </tr>
    <tr><td> 0.85</td> <td> 0.9 </td> <td>Sink        </td> <td>Exp. decay  along $Y$ axis</td> </tr>
    <tr><td> 1.2 </td> <td> 1.1 </td> <td>Source      </td> <td>Exp. growth parallel to $X$ axis</td> </tr>
    <tr><td> 1.5 </td> <td> 1.5 </td> <td>Source      </td> <td>Exp. growth in all directions</td> </tr>
    <tr><td>-0.8 </td> <td> 1.1 </td> <td>Saddle      </td> <td>Exp. growth along $Y$ axis</td> </tr>
    <tr><td>-0.8 </td> <td> 0.5 </td> <td>Sink        </td> <td>Fluctuating exp. decay along $X$ axis</td> </tr>
    <tr><td> 0.95</td> <td>-1.1 </td> <td>Saddle      </td> <td>Fluctuating exp. growth along $Y$ axis</td> </tr>
    <tr><td>-0.8 </td> <td>-1.2 </td> <td>Saddle      </td> <td>Fluctuating exp. growth along $Y$ axis</td> </tr>
</table>


**Conclusions:**

If multiple (two *or more*) variables in a discrete-time model are exponentially growing/decaying *independently* of each other (i.e. the model is *linear* with a *diagonal matrix*), then the resulting behavior is as follows: 
1. Overall behavior: 
    - If both rates have absolute value > 1, then any starting state will grow *away from* the origin. That is, the equilibrium point at the origin is a ***source*** (unstable). 
    - If both rates have absolute value < 1, then any starting state will grow *toward* the origin. That is, the equilibrium point at the origin is a ***sink*** (stable). 
    - If one rate has absolute value < 1 and the other > 1, then a starting state will move inward along one axis, but grow outward along the other. That is, the equilibrium point at the origin is a ***saddle point*** (unstable). 

2. If either rate is negative, the behavior along the corresponding axis will be exponential growth/decay combined with fluctuating back and forth between positive and negative values. 

3. Finally, the long-term behavior will be in the direction of whichever axis has the ***dominant*** rate (or ***dominant eigenvalue***). The dominant rate (eigenvalue) is the one whose **absolute value is greatest**. 
